[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/drive/1xNqUExG_mNv3YbG07uoCPkoA2APDQ2Th#scrollTo=86kBgQQ3DvGF)
      

In [1]:
# !pip install yfinance

In [2]:
import numpy as np
import pandas as pd
import plotly
import scipy.stats as sts
from plotly.subplots import make_subplots
from scipy.special import kolmogorov
import yfinance as yf

plotly.offline.init_notebook_mode(connected=False)

# Загрузка данных
В работе будут использованы котировки 8 японских компаний из различных областей экономики. Все компании входят в биржевой индекс **Nikkei 225**, один из важнейших фондовых индексов Японии. Тикер указан в скобках.

1. [ *Пищевая промышленность* ] Asahi Breweries, Ltd. (2502.T)
2. [ *Телекоммуникации* ] Fujikura - Fujikura Ltd. (5803.T)
3. [ *Тяжёлая промышленность* ] Mitsubishi Heavy Industries, Ltd  (MHVYF)
4. [ *Xимическая промышленность* ] Asahi Kasei Corporation (AHKSY)
5. [ *Электроника* ] Casio Computer Co., Ltd. (CSIOY)
6. [ *Фармацевтическая промышленность* ] Astellas Pharma (ALPMY)
7. [ *Нефтегазовая и нефтехимическая промышленность* ] ENEOS Holdings (5020.T)
8. [ *Банковские услуги* ] Sumitomo Mitsui Financial Group, Inc. (SMFG)

Будем рассматривать дневные котировки за 10 последних лет, т.е. с начала 2012 по конец 2021. Значения технических индикаторов будут рассчитываться по цене закрытия Close, а данные на нормальность будут проверяться по цене Adj Close, чтобы избежать выбросов в данных, которые возникают в силу технический и иных событий на бирже.

In [3]:
## Выгрузим данные из папки data/raw_data

# Массив тикеров
tickers = ['2502.T', '5803.T', 'MHVYF', 'AHKSY', 'CSIOY', 'ALPMY', '5020.T', 'SMFG']
quotations = []  # Список котировок. Stock market quotations - Биржевые котировки

for i in range(len(tickers)):

    ticker_data = yf.download(tickers[i], start='2012-01-01', end='2022-01-01', interval='1d').reset_index()
    # Удалим те записи, в которых цена закрытия пустая
    ticker_data = ticker_data.drop(index=ticker_data[ticker_data['Adj Close'].isna()].index)
    # Добавим в список данных по тикерам, очередной тикер
    quotations.append(ticker_data)


quotations[7].head()

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


Date  Open  High   Low  Close  Adj Close  Volume
0 2012-01-03  5.62  5.71  5.59   5.70       5.70  448700
1 2012-01-04  5.76  5.78  5.73   5.77       5.77  401700
2 2012-01-05  5.71  5.72  5.67   5.69       5.69  156200
3 2012-01-06  5.68  5.68  5.62   5.65       5.65  131800
4 2012-01-09  5.68  5.69  5.65   5.66       5.66  188400

In [4]:
# Графики цен закрытия для всех котировок
close_plots = make_subplots(4, 2, subplot_titles=tickers)

m = 0  # Индекс рассматриваемого тикера
for i in range(1, 5):  # Перебор по строкам
    for j in range(1, 3):  # Перебор по столбцам:
        # Рисуем на i-ой, j-ой позиции график цены закрытия AdjClose
        close_plots.add_scatter(x=quotations[m]['Date'], y=quotations[m]['Adj Close'],
                                marker={'color': 'rgb(16, 106, 91)'},
                                row=i, col=j, showlegend=False)

        close_plots.update_layout()  # Увеличиваем подписи осей
        m += 1  # Переходим к новому тикеру

close_plots.update_layout(title={'text': '<b>Графики цен котировок</b>'})
close_plots.update_layout(height=800)  # Изменяем соотношения осей
close_plots.show(renderer="colab")  # Показываем получившийся график

# Ликвидность котировок
Для оценки ликвидности котировок посчитаем количество торговых дней на каджый год

In [5]:
cnt_sale_days = pd.DataFrame(columns=['Тикер', 'Год', 'Количество рабочих дней'])

# 8 котировок, 10 лет, переберем все тикеры и все года
m = 0  # Номер строки
for i in range(8):
    for year in range(2012, 2022):
        df_i = quotations[i]  # Берем очередные данные
        df_i['Date'] = pd.to_datetime(df_i['Date'], format='%Y-%m-%d')  # Сменим тип на тип datetime
        # Проверяем, чтобы дата была между year и year + 1 и считаем количество таких даты
        cnt_days = sum(
            (pd.Timestamp(f'{year}-01-01') <= df_i['Date']) & (df_i['Date'] < pd.Timestamp(f'{year + 1}-01-01')))
        # Записываем в датасет получившееся значение
        cnt_sale_days.loc[m] = [tickers[i], year, cnt_days]
        m += 1

cnt_sale_days.head()  # Выводим первые 5 строк

Тикер   Год Количество рабочих дней
0  2502.T  2012                     248
1  2502.T  2013                     245
2  2502.T  2014                     244
3  2502.T  2015                     244
4  2502.T  2016                     245

In [6]:
# Группируем данные в нужный вид
amount_workdays = cnt_sale_days.pivot_table(index='Тикер', columns='Год', values='Количество рабочих дней',
                                            aggfunc='first')
amount_workdays

Год     2012  2013  2014  2015  2016  2017  2018  2019  2020  2021
Тикер                                                             
2502.T   248   245   244   244   245   253   261   241   242   245
5020.T   248   245   244   244   245   253   261   241   242   245
5803.T   248   245   244   244   245   253   261   241   242   245
AHKSY    250   252   252   252   252   251   251   252   253   252
ALPMY    250   252   252   252   252   251   251   252   253   252
CSIOY    250   252   252   252   252   251   251   252   253   252
MHVYF    250   252   252   252   252   251   251   252   253   252
SMFG     250   252   252   252   252   251   251   252   253   252

# Логарифмическая доходность
Логарифмическая доходность $r_i$ определяется отношением цен на момент $t_1$ к моменту $t_0$:
$$ r_i = \ln\left(\frac{P_{t_1}}{P_{t_0}}\right) = \ln(P_{t_1}) - \ln(P_{t_0}) $$

где $P_{t_0}$ и $P_{t_1}$ - цены котировок на двух соседних торговых днях.


In [7]:
# Сформируем список преобразованных котировок. Сделаем столбцы доходности и значение индикатора
quotations_transformed = []

for i in range(8):
    df_i = quotations[i].copy()
    # Находим логарифмическую доходность по формуле выше
    log_profitability = np.log(df_i['Adj Close'].values[1:]) - np.log(df_i['Adj Close'].values[:-1])
    # Первое значение пропущено, т.к. для рассчета доходности нужна предыдущая цена
    df_i['Лог доходность'] = [np.nan] + list(log_profitability)

    # Сохраняем преобразованные данные
    quotations_transformed.append(df_i)

quotations_transformed[0].head()

Date    Open    High     Low   Close    Adj Close   Volume  \
0 2012-01-04  1711.0  1718.0  1700.0  1704.0  1407.867310   906300   
1 2012-01-05  1695.0  1703.0  1689.0  1689.0  1395.474121   635700   
2 2012-01-06  1704.0  1705.0  1686.0  1697.0  1402.083984  1260900   
3 2012-01-10  1705.0  1707.0  1693.0  1703.0  1407.041016   997500   
4 2012-01-11  1704.0  1714.0  1695.0  1711.0  1413.650635  1405300   

   Лог доходность  
0             NaN  
1       -0.008842  
2        0.004725  
3        0.003529  
4        0.004687

# В нашей работе рассмотрим технический индикатор - ROC
**ROC - Rate of Change**

ROC - скорость изменения показывает скорость изменения цены. ROC - это отношение дельты цены на текущий период и цены на $n$ периодов назад к цене $n$ периодов назад. В нашей работы мы примем $n = 7$ и период - день. То есть индикатор будет показывать недельную доходность актива. Формула:
$$\operatorname{ROC}_7 = \frac{P_t - P_{t - 7}}{P_{t - 7}}$$

Также ее можно умножить на $100%$ для перехода к процентам.
Но в нашей работе мы будем разделять данные на два класса. Первый класс - данные, у которых индикатор отрицательный, второй класс - индикатор положительный. Поэтому перевод индикатора в проценты для нас нерелевантен.

In [8]:
# Добавим значения индиктора в наши даннные и удалим пропуски
for i in range(8):
    # Берем i-ые данные
    df_i = quotations_transformed[i].copy()
    # Считаем значение индикатора на каждую дату
    roc_indicator = (df_i['Adj Close'].values[7:] - df_i['Adj Close'].values[:-7]) / df_i['Adj Close'].values[:-7]
    # Сохраняем значение индикатора
    df_i['Значение ROC'] = [np.nan] * 7 + list(roc_indicator)
    # Удаляем пропуски по строкам
    df_i = df_i.dropna()
    # Сохраняем датасет обратно в список
    quotations_transformed[i] = df_i

quotations_transformed[0].head()

Date    Open    High     Low   Close    Adj Close   Volume  \
7  2012-01-16  1719.0  1722.0  1707.0  1716.0  1417.781982  1013600   
8  2012-01-17  1722.0  1733.0  1720.0  1729.0  1428.522583   917700   
9  2012-01-18  1723.0  1733.0  1707.0  1717.0  1418.608032  1234000   
10 2012-01-19  1716.0  1723.0  1701.0  1705.0  1408.693604  1455200   
11 2012-01-20  1735.0  1745.0  1724.0  1731.0  1430.174927  1563400   

    Лог доходность  Значение ROC  
7        -0.001165      0.007042  
8         0.007547      0.023683  
9        -0.006965      0.011785  
10       -0.007013      0.001175  
11        0.015134      0.011689

# Проверим распределение значений индикатора
 Посчитаем количество дней, когда индикатор был меньше или не меньше нуля.

In [9]:
roc_table = pd.DataFrame(columns=['Тикер', 'Год', 'ROC >= 0', 'ROC < 0'])

m = 1
for i in range(8):
    for year in range(2012, 2022):
        df_i = quotations_transformed[i]
        df_i = df_i[df_i['Date'].dt.year == year]
        cnt_positive = sum(df_i['Значение ROC'] >= 0)  # Считаем количество неотрицательных значений индикатора
        cnt_negative = sum(df_i['Значение ROC'] < 0)  # -- || -- отрицательных
        roc_table.loc[m] = [tickers[i], year, cnt_positive, cnt_negative]
        m += 1

roc_table.head()

Тикер   Год ROC >= 0 ROC < 0
1  2502.T  2012      132     109
2  2502.T  2013      157      88
3  2502.T  2014      139     105
4  2502.T  2015      137     107
5  2502.T  2016      123     122

In [10]:
# Сформируем сводную таблицу
df = roc_table.pivot_table(values=['Тикер', 'ROC >= 0', 'ROC < 0'], index='Год', columns='Тикер', aggfunc='first')
df.columns = df.columns.swaplevel()  # Переставим местами названия уровней столбцов
df = df.sort_index(axis='columns', level=0).T  # Отсортируем по названию столбцов
df

Год              2012  2013  2014  2015  2016  2017  2018  2019  2020  2021
Тикер                                                                      
2502.T ROC < 0    109    88   105   107   122    76   155   100   129   109
       ROC >= 0   132   157   139   137   123   177   106   141   113   136
5020.T ROC < 0    120    91   124   108   123    87   142   116   137   108
       ROC >= 0   121   154   120   136   122   166   119   125   105   137
5803.T ROC < 0    115    90   109   104   122   110   159   103   128   104
       ROC >= 0   126   155   135   140   123   143   102   138   114   141
AHKSY  ROC < 0    115   103    99   144   116    91   132   106   133   137
       ROC >= 0   128   149   153   108   136   160   119   146   120   115
ALPMY  ROC < 0    116   113   103   124   139   131   105   114   130   113
       ROC >= 0   127   139   149   128   113   120   146   138   123   139
CSIOY  ROC < 0     72   114   102   102   142   113   119    86   126   135
       ROC >= 0   171   138   150   150   110   138   132   166   127   117
MHVYF  ROC < 0    108   105   114   129   118   134   100    96   146   151
       ROC >= 0   135   147   138   123   134   117   151   156   107   101
SMFG   ROC < 0    103   108   151   129   118   117   150   104   136   125
       ROC >= 0   140   144   101   123   134   134   101   148   117   127

# Критерий Пирсона
Пусть есть $X_{1}, X_{2}, \dots, X_{(n)}$ - выборка размера $n$ из генерального распределения $\mathcal{L}(\theta)$.

Гипотеза $H_0$ состоит в том, что выборка $X_{1}, X_{2}, \dots, X_{(n)}$ распределена по какому-то преполагаемому закону $F(x)$.
В нашей работе мы будем проверять гипотезу нормальности логарифмической доходности, то есть предполагать, что $X_i \sim N(\mu, \sigma^2)$

Сгруппируем наблюдения по $k$ непересекающимся интервалам: $ t_{(0)} < t_{(1)} < \dots < t_{(k)} $. Затем посчитаем количество наблюдений попавшее в каждый интервал и обозначим их как $n_1, n_2, \dots, n_3$. Таких наблюдений мы получим $k$ штук.
Вероятность попадания в $i$-ый интервал $p_i = P(t_{(i - 1)} < X \leq t_{(i)}) = P(X \leq t_{(i)}) - P(X \leq t_{(i - 1)}) = F(t_{(i)}) - F(t_{(i - 1)})$. Тогда ожидаемое количество наблюдений, попавщих в интервал $i$ будет равно $n \cdot p_i$.

Теперь статистику $\chi^2_n$ Пирсона мы вычисляем по формуле:
$$\chi^2_n = \sum_{i = 1}^{n} \frac{(n_i - p_i \cdot n)^2}{p_i \cdot n}$$

Эта статистика при больших $n$ стремится к распределению $\chi^2_{k-m-1} = \chi^2_{k-2-1} $, $m$ - количество оцениваемых параметров.

Для оценивания параметров $\mu, \sigma$ можем использовать минимизация $\chi^2$, или метод максимального правдоподобия.
Можно показать, что оценки параметров нормального распределения методом максимального правдоподобия будут равны:

$$\hat \mu = \overline X, \qquad \hat \sigma^2 = \frac{1}{n} \sum_{i=1}^{n}(X_i - \overline X) ^ 2$$


In [11]:
def chi_square_test(x, mu=0, sigma=1):
    # инициализируем нормальное распределение
    norm = sts.norm(mu, sigma)  # norm.cdf - функция распределения F(x)

    # Сначала разобьем на интервалы наблюдаемые значения
    n = len(x)
    k = 1 + int(np.log2(n))  # По правилу Стёрджеса найдем нужное количетсво разбиений
    t_list = np.linspace(min(x), max(x), k - 1)  # Создаем разбиение
    t_list[0], t_list[-1] = -np.inf, np.inf
    x_obs = []  # Наблюдаемые значения для разбиения. observation - наблюдаемые.
    x_exp = []  # Ожидаемые значения. expected - ожидаемое

    amount_obs, amount_exp = 0, 0
    for i in range(0, k - 2):  # проходимся по внутренним интервалам
        amount_obs += sum((t_list[i] <= x) & (x < t_list[i + 1]))  # Считаем значения попавшие в интервал i
        amount_exp += norm.cdf(t_list[i + 1]) - norm.cdf(t_list[i])  # Считаем вероятность p_i и умножаем на n

        if amount_exp > 1e-4:  # Избегаем деления на околонулевые значения
            x_obs.append(amount_obs)  # Записываем
            x_exp.append(amount_exp * n)  # Записываем
            amount_obs, amount_exp = 0, 0

    # Вычисляем статистику по формуле
    chi2 = sum((np.array(x_obs) - np.array(x_exp)) ** 2 / np.array(x_exp))

    # ddof = m - параметр количества оцениваемых параметров
    return chi2, sts.chi2(k - 2 - 1).sf(chi2)  # Возращает статистику и p-value


# Тестирование функции
x = sts.norm().rvs(1000)
chi_square_test(x)

(7.394565545186481, 0.3889848190614862)

# Критерий согласия Колмогорова
Как и в критерии хи-квадрат выдвигается гипотеза $H_0: F_n(x) = F(x)$ - выборка принадлжеит какому-то теоритическому закону распределения.

В этом критерии рассматривается следующая статистика: $\displaystyle \sqrt{n}D_n = \sqrt{n} \sup_{x\in \mathbb{R}} \left| F_n(x) - F(x) \right|$.
По теореме Колмогорова при условии, что гипотеза $H_0$ - верна, то $\forall t>0\colon\lim_{n\to\infty}P(\sqrt{n}D_n\leqslant t)=K(t)=\sum_{j=-\infty}^{+\infty}(-1)^j e^{-2j^2t^2}$ - распределение Колмогорова.

Алгоритм принятия решения следующий. Если полученная стастика больше процентной точки $K_\alpha$, то гипотеза отвергается на уровне значимости $\alpha$. Либо мы можем рассмотреть p-value для правосторонней гипотезы, что эквивалентно. В работе применяется второй метод.

Для рассчета статистики мы будем использовать следующую формулу: $D_n = \max_{1 \le i \le n} \left\{F(x_{(i)}) - \frac{i - 1} {n}, \frac{i}{n} - F(x_{(i)})\right\}$

In [12]:
def kolmogorov_norm_test(x, mu=0, sigma=1):
    d = 0  # Инициализируем D
    n = len(x)
    norm = sts.norm(mu, sigma)  # Инициализируем нормальное распределение
    x = sorted(x)  # Получаем вариационный ряд
    for i in range(n):  # Перебор по всем значениям выборки
        d = max(d, norm.cdf(x[i]) - i / n, (i + 1) / n - norm.cdf(x[i]))  # Формула выше

    return d, kolmogorov(n ** 0.5 * d)  # Возращаем стастику D и p_value


# Тестирование функции
x = sts.norm().rvs(1000)
kolmogorov_norm_test(x)

(0.050678624774609604, 0.011754736178841667)

# Модельные данные
Для проверки алгоритмов проведем много экспериментов (порядка $2000$) и проверим количество отвергнутых гипотез. На уровне значимости $\alpha = 0.5$ ожидаем увидеть $5\%$ отвергнутых гипотез


In [13]:
N = 2000
chi_pvs = []  # Будем записывать p-значения
kolm_pvs = []

for i in range(N):
    x_norm_rvs = sts.norm().rvs(100)  # Генерируем выборку размера 100
    t, pv = chi_square_test(x_norm_rvs)  # Вычисляем статистику и p_value
    chi_pvs.append(pv)

for i in range(N):
    x_norm_rvs = sts.norm().rvs(100)  # Генерируем выборку размера 100
    t, pv = kolmogorov_norm_test(x_norm_rvs)  # Вычисляем статистику и p_value
    kolm_pvs.append(pv)

print(f'Процент отвергнутых гипотез хи-квадрат: {sum(np.array(chi_pvs) < 0.05) / N * 100: .1f}%')
print(f'Процент отвергнутых гипотез Колмогоров: {sum(np.array(kolm_pvs) < 0.05) / N * 100: .1f}%')

Процент отвергнутых гипотез хи-квадрат:  6.5%
Процент отвергнутых гипотез Колмогоров:  4.9%


In [14]:
pvalue_plots = make_subplots(1, 2, subplot_titles=['<b>P-значения для Хи-Квадрат</b>',
                                                   '<b>P-value для критерия Колмогорова</b>'])

pvalue_plots.add_histogram(x=chi_pvs, row=1, col=1, showlegend=False, 
                           xbins={'start': 0, 'end': 1, 'size': 0.1})
pvalue_plots.update_yaxes(title={'text': 'Количество'})  # Обновляем ось у
pvalue_plots.update_xaxes(title={'text': 'p-value'})  # Обновляем ось x


pvalue_plots.add_histogram(x=kolm_pvs, row=1, col=2, showlegend=False, 
                           xbins={'start': 0, 'end': 1, 'size': 0.1})
pvalue_plots.update_yaxes(title={'text': 'Количество'})  # Обновляем ось у
pvalue_plots.update_xaxes(title={'text': 'p-value'})  # Обновляем ось x

pvalue_plots.update_layout(title={'text': '<b>Распределение p-value для двух критериев</b>'})
pvalue_plots.show(renderer="colab")  # Показываем получившийся график

# Оценка мощности хи-вадрат Пирсона
Для оценки мощности выдвенем четыре гипоетезы
1) $H_1$: Значения логарифмической доходности принадлежат распределению Стьюдента с 10 степенями свободы
2) $H_1$: Значения логарифмической доходности принадлежат распределению Вейбулла с параметрами $\lambda = 1, k = 2$
3) $H_1$: Значения логарифмической доходности принадлежат распределению Коши с параметрами $x_0 = 1, \lambda = 5$
4) $H_1$: Значения логарифмической доходности принадлежат равномерному распределению на отрезке $[-1, 2]$

Проведем по 500 экспериментов, в которых гипотеза $H_0$ будет сложной гипотезой, того что данные распределены нормально. Оценки параметров будут находиться с помощью метода максимального правдоподобия.


In [15]:
import plotly.express as px

x = np.linspace(-2, 3, 500)
ditrs_plot = px.line({'x': x,
                      'Нормальное': sts.norm(0.5, 1).pdf(x),
                      'Стьюдента': sts.t(10).pdf(x),
                      'Вейбулла': sts.weibull_min(2).pdf(x),
                      'Коши': sts.cauchy().pdf(x),
                      'Равномерное': sts.uniform(-1, 3).pdf(x)},
                     # Для равномерного распределения надо задать левую точку и длину
                     x='x', y=['Нормальное', 'Стьюдента', 'Вейбулла', 'Коши', 'Равномерное'],
                     title='<b>Графики плотностей распределений</b>',
                     color_discrete_sequence=['rgb(0, 122, 63)', 'rgb(0, 82, 140)', 'rgb(0, 41, 23)',
                                              'rgb(254, 152, 102)', 'rgb(184, 0, 0)'])

ditrs_plot.update_layout(legend_title_text='')
ditrs_plot.update_yaxes(title={'text': 'f(x)'})
ditrs_plot.show(renderer='colab')

In [16]:
N = 500  # Количество экмпериментов
powers = pd.DataFrame(columns=['Альтернативная гипотеза', 'Мощность'])  # Инициализировали датасет
names = ['Стьюдента', 'Вейбулла', 'Коши', 'Равномерное']  # Названия распределений
distributions = [sts.t(10).rvs, sts.weibull_min(2).rvs, sts.cauchy().rvs,
                 sts.uniform(-1, 3).rvs]  # Инициализировали распределения
p_values = [[], [], [], []]  # Будем сохранять p-значения для каждого распределения

for i in range(4):
    power = 0  # Счетчик отвержения гипотезы H0 в пользу H1
    for _ in range(N):
        rvs_sample = distributions[i](300)  # Генерируем данные из распределения гипотезы H1
        t, pv = chi_square_test(rvs_sample, rvs_sample.mean(), rvs_sample.std())  # Вычисляем p_value
        p_values[i].append(pv)
        if pv < 0.05:  # Считаем количество отвержений
            power += 1
    powers.loc[i] = [names[i], power / N]

powers

Альтернативная гипотеза  Мощность
0               Стьюдента     0.214
1                Вейбулла     0.574
2                    Коши     0.894
3             Равномерное     0.952

In [17]:
power_pv_plots = make_subplots(2, 2, subplot_titles=names)

for i in range(4):
    power_pv_plots.add_histogram(x=p_values[i], row=i // 2 + 1, col=i % 2 + 1, showlegend=False,
                                 xbins={'start': 0, 'end': 1, 'size': 0.1}, name=names[i],
                                 marker={'color': 'rgb(16, 106, 91)'})

    power_pv_plots.update_yaxes(title={'text': 'Количество'})  # Обновляем ось у
    power_pv_plots.update_xaxes(title={'text': 'p-value'})  # Обновляем ось x

power_pv_plots.update_layout(
    title={'text': '<b>Распредения p-значений при верной гипотезе H1</b>'}, height=600) 
power_pv_plots.show(renderer='colab')

# Настоящие данные
Проведем проверку на нормальность наших данных

##  Визуальный анализ
Взглянем на графики при разных значениях индикатора

In [18]:
# Графики цен закрытия для всех котировок
profits_roc_positive = make_subplots(4, 2, subplot_titles=tickers)

m = 0  # Индекс рассматриваемого тикера
for i in range(1, 5):  # Перебор по строкам
    for j in range(1, 3):  # Перебор по столбцам:
        # Рисуем на i-ой, j-ой распределение лог доходности при ROC >= 0
        df_i = quotations_transformed[m]
        df_i = df_i[df_i['Значение ROC'] >= 0]
        profits_roc_positive.add_histogram(x=df_i['Лог доходность'],
                                           marker={'color': 'rgb(16, 106, 91)'},
                                           row=i, col=j, showlegend=False)
        m += 1  # Переходим к новому тикеру

# Ставим заголовок этой группе графиков
profits_roc_positive.update_layout(
    title={'text': '<b>Распределения лог доходностей при ROC >= 0 </b>'})
profits_roc_positive.update_layout(height=800)
profits_roc_positive.show(renderer='colab')  # Показываем получившийся график

In [19]:
# Графики цен закрытия для всех котировок
profits_roc_positive = make_subplots(4, 2, subplot_titles=tickers)

m = 0  # Индекс рассматриваемого тикера
for i in range(1, 5):  # Перебор по строкам
    for j in range(1, 3):  # Перебор по столбцам:
        # Рисуем на i-ой, j-ой распределение лог доходности при ROC >= 0
        df_i = quotations_transformed[m]
        df_i = df_i[df_i['Значение ROC'] < 0]
        profits_roc_positive.add_histogram(x=df_i['Лог доходность'],
                                           marker={'color': 'rgb(16, 106, 91)'},
                                           row=i, col=j, showlegend=False)
        m += 1

# Ставим заголовок этой группе графиков
profits_roc_positive.update_layout(
    title={'text': '<b>Распределения лог доходностей при ROC < 0 </b>'}, height=800)
profits_roc_positive.show(renderer='colab')  # Показываем получившийся график

# Численный анализ
## $\chi^2$ Пирсона

In [20]:
# Таблица - тикер котировки, значение ROC, p-значение, Отвергается H0?
chi_test_table_data = pd.DataFrame(columns=['Тикер', 'ROC', 'P-значение', 'Отвергается H0?'])
m = 0
for i in range(len(tickers)):  # Перебор по тикерам
    # Вычисляем значения для ROC >= 0
    df_i = quotations_transformed[i]
    df_i = df_i[df_i['Значение ROC'] >= 0]
    log_profit_i = df_i['Лог доходность']
    t, pv = chi_square_test(log_profit_i, log_profit_i.mean(), log_profit_i.std())
    if pv >= 0.05:
        conclusion = 'Не отвергается'
    else:
        conclusion = 'Отвергается'
    chi_test_table_data.loc[m] = [tickers[i], 'ROC >= 0', pv, conclusion]
    m += 1

    # Вычисляем значения для ROC < 0
    df_i = quotations_transformed[i]
    df_i = df_i[df_i['Значение ROC'] < 0]
    log_profit_i = df_i['Лог доходность']
    t, pv = chi_square_test(log_profit_i, log_profit_i.mean(), log_profit_i.std())
    if pv >= 0.05:
        conclusion = 'Не отвергается'
    else:
        conclusion = 'Отвергается'
    chi_test_table_data.loc[m] = [tickers[i], 'ROC < 0', pv, conclusion]
    m += 1

chi_pivot = chi_test_table_data.pivot_table(values='Отвергается H0?', index='Тикер', 
                                            columns='ROC', aggfunc='first')
chi_pivot

ROC         ROC < 0     ROC >= 0
Тикер                           
2502.T  Отвергается  Отвергается
5020.T  Отвергается  Отвергается
5803.T  Отвергается  Отвергается
AHKSY   Отвергается  Отвергается
ALPMY   Отвергается  Отвергается
CSIOY   Отвергается  Отвергается
MHVYF   Отвергается  Отвергается
SMFG    Отвергается  Отвергается

In [21]:
chi_pivot_pv = chi_test_table_data.pivot_table(values='P-значение', index='Тикер', columns='ROC',
                                               aggfunc='first').round(6)
chi_pivot_pv

ROC     ROC < 0  ROC >= 0
Тикер                    
2502.T      0.0  0.000000
5020.T      0.0  0.000030
5803.T      0.0  0.000000
AHKSY       0.0  0.000000
ALPMY       0.0  0.000004
CSIOY       0.0  0.000000
MHVYF       0.0  0.000000
SMFG        0.0  0.000000

In [22]:
# Таблица - тикер котировки, значение ROC, p-значение, Отвергается H0?
kolmogorov_test_table = pd.DataFrame(columns=['Тикер', 'ROC', 'P-значение', 'Отвергается H0?'])
m = 0
for i in range(len(tickers)):  # Перебор по тикерам
    # Вычисляем значения для ROC >= 0
    df_i = quotations_transformed[i]
    df_i = df_i[df_i['Значение ROC'] >= 0]
    log_profit_i = df_i['Лог доходность']
    t, pv = kolmogorov_norm_test(log_profit_i, log_profit_i.mean(), log_profit_i.std())
    if pv >= 0.05:
        conclusion = 'Не отвергается'
    else:
        conclusion = 'Отвергается'
    kolmogorov_test_table.loc[m] = [tickers[i], 'ROC >= 0', pv, conclusion]
    m += 1

    # Вычисляем значения для ROC < 0
    df_i = quotations_transformed[i]
    df_i = df_i[df_i['Значение ROC'] < 0]
    log_profit_i = df_i['Лог доходность']
    t, pv = kolmogorov_norm_test(log_profit_i, log_profit_i.mean(), log_profit_i.std())
    if pv >= 0.05:
        conclusion = 'Не отвергается'
    else:
        conclusion = 'Отвергается'
    kolmogorov_test_table.loc[m] = [tickers[i], 'ROC < 0', pv, conclusion]
    m += 1

kolmogorov_pivot = kolmogorov_test_table.pivot_table(values='Отвергается H0?', index='Тикер', columns='ROC',
                                                     aggfunc='first')
kolmogorov_pivot

ROC         ROC < 0     ROC >= 0
Тикер                           
2502.T  Отвергается  Отвергается
5020.T  Отвергается  Отвергается
5803.T  Отвергается  Отвергается
AHKSY   Отвергается  Отвергается
ALPMY   Отвергается  Отвергается
CSIOY   Отвергается  Отвергается
MHVYF   Отвергается  Отвергается
SMFG    Отвергается  Отвергается

In [23]:
kolmogorov_pivot_pv = kolmogorov_test_table.pivot_table(values='P-значение', index='Тикер', columns='ROC',
                                                        aggfunc='first').round(6)
kolmogorov_pivot_pv

ROC      ROC < 0  ROC >= 0
Тикер                     
2502.T  0.000799  0.000007
5020.T  0.003663  0.008287
5803.T  0.002422  0.000006
AHKSY   0.000007  0.000615
ALPMY   0.000236  0.006440
CSIOY   0.000000  0.000000
MHVYF   0.000000  0.000000
SMFG    0.000004  0.000008

# Заключение
Как мы можем наблюдать логарифмическая доходность на японском рынке, а именно 8 котировок, которые мы рассмотрели выше, не подчиняется нормальному закону распределения.
Все тесты на все бумаги отрицают гипотезу $H_0$ - нормальность логарифмической доходности.